## Ukesoppgaver IN2070: Kompresjon og Koding II

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import os
import heapq

from PIL import Image
from numpy import fft
from urllib.request import urlretrieve

# Setter opp noen bedre standardargumenter for plotting med bilder
plt.rcParams['figure.figsize'] = [10.24, 7.68]
plt.rcParams['image.cmap'] = 'gray'

In [ ]:
# Last ned testbilde vi skal bruke
url = '/studier/emner/matnat/ifi/IN2070/h23/undervisningsmateriale/bilder/lena.png'
if not os.path.isfile('lena.png'):
    urllib.request.urlretrieve(url, 'lena.png')
    
# Laster inn bilde som array med PIL og normaliserer til flyttall
image = np.array(Image.open('lena.png')) / 255

## Oppgave 1:

I denne oppgaven skal vi kode DCT-II transformen; først med en naiv matrisemultiplikasjon, så med en fast Fourier transform (`fft`) variant.

### 1a: Enkel DCT

Skriv en funksjon som regner ut DCT-II matrisen. Formelen er gitt ved

$$
\begin{align}
    \tilde x_k = \sum_{n=0}^{N-1} x_n \cos\big(k\pi (n + 1/2) / N\big),
\end{align}
$$
hvor $(x_n)_{n=0}^{N-1}$ er et 1D signal (tenk rad eller kolonne i bildet). 
Skriv også en funksjon som anvender seperabilitet for bilder for å regne ut DCT transformen gitt matrisen.
**Merk**: DCT utregningen er i standardform, og ikke ortonormal

**Tips:**
- Vi vil ha indekser for $k=0,...,N-1$ kolonner og $n=0,...,N-1$ rader i bildet. Her kan `np.meshgrid` benyttes med hell.
- Gitt arrayene `k, n` så er det enkelt å vektorisere utregningene i Numpy med `np.cos`.
- For separabilitet har vi $\tilde X = \mathcal{C} X \mathcal{C}^{\intercal}$ der $X$ er orginalbildet med dimensjon $N \times N$.
- Hva skjer hvis bildet har forskjellige dimensjoner for høyde og bredde? Tenk litt på dette.

### 1b: Invers DCT

Invers til DCT-II fra 1a (gjerne kalt DCT-III eller iDCT) er gitt ved

$$
\begin{align}
    x_k = \frac{2}{N}\Big(\frac{1}{2}x_0 + \sum_{n=1}^{N-1} \tilde x_n \cos\big(n\pi (k + 1/2) / N\big)\Big),
\end{align}
$$

Lag en funksjon som regner ut iDCT matrisen. Bekreft implementasjonen ved å skrive en funksjon som foretar iDCT og inverter deretter transformen fra 1a.

In [ ]:
...

## Oppgave 2:


### 2a: WHT Matrise
Skriv en funksjon som regner ut Walsh-Hademard transformen. Bruk Hademard form av matrisen, gitt ved rekursjonen
$$
W^{(2n)} = \begin{bmatrix}
W^{(n)} & W^{(n)}\\
W^{(n)} & -W^{(n)}\\
\end{bmatrix}
$$

og bruk nullutvidelse for å utvide bildet til nærmeste potensverdi av 2.


### 2b: WHT vs. DCT

Regn ut WHT og DCT for bildet, og estimer glissenhet (sparsity) ved å ta det såkalte *Euclid-in-a-Taxicab* forholdet gitt ved

$$
\frac{\lVert x \rVert_1}{\lVert x \rVert_2} = \frac{\sum_{m=0}^{N-1} \lvert x_m \rvert}{\sqrt{\sum_{n=0}^{N-1} x_n^2}}.
$$

Jo lavere forhold (teoretisk minimum 1), jo mer glissen er transformasjonen.

In [ ]:
...

## Oppgave 3: LZW transform

### 3a: LZW Enkoder

Skriv en LZW Enkoder ved å benytte følgende steg:

1. **Initialisering**: Start med en ordliste (dictionary) som inneholder alle tegn i ASCII-tegnsettet, hver med sin unike kode. 
2. **Lesing**: Les inn tegn fra dataene som skal komprimeres sekvensielt.
3. **Søk i ordlisten**: For hver nye tegnsekvens, sjekk om sekvensen finnes i ordlisten.
    - Hvis den finnes, fortsett å legge til tegn til sekvensen og gjenta søket.
    - Hvis den ikke finnes, utfør følgende trinn:
4. **Lagre til ordlisten**: Legg til den nye tegnsekvensen i ordlisten med en ny unik kode.
5. **Skriv ut kode**: Skriv ut koden som tilsvarer den lengste sekvensen som finnes i ordlisten.
6. **Fortsett prosessen**: Start den nye sekvensen med det tegnet som ikke ble funnet i ordlisten og gjenta prosessen.
7. **Slutten av data**: Når det ikke er flere tegn å lese, skriv ut koden for den siste sekvensen.
8. **Output**: Komprimerte data vil være en sekvens av koder som representerer de lengre strengene i originaldataene.


**Tips**: ASCII kodesettet kan hentes ut ved `chr(i) for i in range(256)`. Det kan være lurt å teste med en liten streng underveis.

### 3b: LZW Dekoder

Skriv så en LZW dekoder, ved følgende steg:

1. **Initialisering**: Opprett en ordliste (dictionary) identisk med den som ble brukt i kompressoren.
2. **Les første kode**: Les den første koden fra de komprimerte dataene og oversett den til det tilsvarende tegnet eller tegnsekvensen fra ordlisten. Skriv ut denne sekvensen til output.
3. **Forrige sekvens**: Lagre den dekodede tegnsekvensen som den forrige sekvensen.
4. **Prosesser påfølgende koder**: For hver påfølgende kode:   
    - **Finn i ordlisten**: Oversett koden til en sekvens ved å se den opp i ordlisten.
        - Hvis koden ikke finnes i ordlisten, er det en spesiell situasjon. Sekvensen må være den forrige sekvensen pluss dens første tegn. Generer denne sekvensen.
        - Hvis koden finnes, er det direkte oversettelsen av koden til en sekvens.
    - **Skriv ut sekvens**: Skriv ut den dekodede sekvensen til output.
    - **Oppdater ordlisten**: Legg til en ny sekvens i ordlisten som er lik den forrige sekvensen pluss det første tegnet i den nåværende dekodede sekvensen.
    - **Oppdater forrige sekvens**: Sett den nåværende dekodede sekvensen som den forrige sekvensen for neste iterasjon.
5. **Fortsett til enden**: Fortsett prosessen til alle kodene er lest og dekodet.
6. **Output**: Det dekodede outputtet skal nå være en eksakt kopi av de originale dataene før de ble komprimert.


### 3c: Enkod teksten

Den vakre teksten `greatlyric` gir frysninger til alle som våger lese den. 
Enkod teksten, sjekk at den dekodes korrekt, og regn ut kompresjonsraten gitt ved 

$$
\frac{\mathrm{original\,\,lengde}}{\mathrm{enkodet\,\,lengde}}
$$

Er kompresjonsraten som forventet?

In [ ]:
...

In [ ]:
greatlyric = '''
Nu reser jag till Söderns land
Till varm och solig strand
Jag surfar över vågorna
Som tar mig in till land
Där flickorna, de dansar
Hula-hula natten lång
I takt med vindens melodi
Sjunger vi en sång
I vårt eget Blue Hawaii
I vårt eget Blue Hawaii
Blue Hawaii, vårt eget Blue Hawaii
Hand i hand på en solig strand
Nu är jag här i Söderns land
I mitt eget Blue Hawaii
Hon binder en fin blomsterkrans
Och hänger runt min hals
Där under sköna palmerna
Jag bjuder upp till dans
Vi vandrar tätt intill varann
I kvällens solnedgång
Och ukelelen spelar upp
Havets egen sång
I vårt eget Blue Hawaii
I vårt eget Blue Hawaii
Blue Hawaii, vårt eget Blue Hawaii
Hand i hand på en solig strand
Nu är jag här i Söderns land
I mitt eget Blue Hawaii
I vårt eget Blue Hawaii
I vårt eget Blue Hawaii
Blue Hawaii, vårt eget Blue Hawaii
Hand i hand på en solig strand
Nu är jag här i Söderns land
I mitt eget Blue Hawaii
'''

In [ ]:
...